In [1]:
import numpy as np
import matplotlib.pyplot as plt
from google.colab import files
from IPython.display import display, HTML, clear_output, Javascript
import ipywidgets as widgets
import io
import base64

# Upload button for video
upload_button = widgets.Button(description='Upload Video')
output = widgets.Output()

def on_upload_clicked(b):
    clear_output(wait=True)
    print("Please upload a video file...")
    uploaded = files.upload()

    if uploaded:
        # Get the first file
        for filename, content in uploaded.items():
            # Convert video to base64 for embedding in HTML
            video_b64 = base64.b64encode(content).decode()
            display_video_with_zoom(video_b64, filename)
            break

upload_button.on_click(on_upload_clicked)
display(upload_button, output)

def display_video_with_zoom(video_b64, filename):
    """Display video with zoom functionality"""

    # HTML for video player with zoom controls
    html_content = f"""
    <div style="margin: 20px auto; text-align: center;">
        <h3>{filename}</h3>
        <div id="player-container" style="position: relative; width: 800px; height: 450px; margin: 0 auto;
                                         border: 2px solid #ddd; border-radius: 8px; overflow: hidden; background-color: #000;">
            <div id="video-container" style="position: absolute; width: 100%; height: 100%; transform-origin: 0 0;">
                <video id="video-player" controls style="width: 100%; height: 100%; display: block;">
                    <source src="data:video/mp4;base64,{video_b64}" type="video/mp4">
                    Your browser does not support the video tag.
                </video>
            </div>
        </div>

        <div style="margin-top: 15px; text-align: center;">
            <div style="display: inline-flex; align-items: center; gap: 10px; margin-bottom: 10px;">
                <button id="zoom-out" style="background-color: #2196F3; color: white; border: none;
                                           border-radius: 4px; padding: 5px 15px; cursor: pointer; font-size: 16px;">−</button>
                <div id="zoom-level" style="background-color: #fff; padding: 5px 10px; border-radius: 4px;
                                          border: 1px solid #ddd; min-width: 50px; text-align: center;">100%</div>
                <button id="zoom-in" style="background-color: #2196F3; color: white; border: none;
                                          border-radius: 4px; padding: 5px 15px; cursor: pointer; font-size: 16px;">+</button>
                <button id="zoom-reset" style="background-color: #f44336; color: white; border: none;
                                             border-radius: 4px; padding: 5px 15px; cursor: pointer; font-size: 16px;">Reset</button>
            </div>
        </div>

        <div style="margin-top: 15px; background-color: #f0f0f0; padding: 10px; border-radius: 5px; display: inline-block;">
            <b>Controls:</b>
            <ul style="text-align: left; margin-bottom: 0;">
                <li>Use mouse wheel to zoom in/out</li>
                <li>Click and drag to pan when zoomed in</li>
                <li>Double-click to reset zoom</li>
            </ul>
        </div>
    </div>
    """

    # JavaScript for zoom functionality
    js_code = """
    // Wait for the elements to be fully loaded
    setTimeout(function() {
        const playerContainer = document.getElementById('player-container');
        const videoContainer = document.getElementById('video-container');
        const videoPlayer = document.getElementById('video-player');
        const zoomInBtn = document.getElementById('zoom-in');
        const zoomOutBtn = document.getElementById('zoom-out');
        const zoomResetBtn = document.getElementById('zoom-reset');
        const zoomLevelDisplay = document.getElementById('zoom-level');

        if (!playerContainer || !videoContainer || !videoPlayer) {
            console.error('Required elements not found');
            return;
        }

        // Set initial values
        let scale = 1;
        let posX = 0;
        let posY = 0;
        let startX = 0;
        let startY = 0;
        let startPosX = 0;
        let startPosY = 0;
        let isPanning = false;
        const MIN_SCALE = 1;
        const MAX_SCALE = 10;
        const ZOOM_STEP = 0.2;

        // Update the transform
        function updateTransform() {
            videoContainer.style.transform = `translate(${posX}px, ${posY}px) scale(${scale})`;
            zoomLevelDisplay.textContent = `${Math.round(scale * 100)}%`;
        }

        // Reset zoom and position
        function resetZoomAndPosition() {
            scale = 1;
            posX = 0;
            posY = 0;
            updateTransform();
        }

        // Handle wheel event for zoom
        playerContainer.addEventListener('wheel', function(e) {
            e.preventDefault();

            // Get mouse position relative to container
            const rect = playerContainer.getBoundingClientRect();
            const mouseX = e.clientX - rect.left;
            const mouseY = e.clientY - rect.top;

            // Calculate zoom direction and new scale
            const delta = e.deltaY < 0 ? 1 : -1;
            const zoomFactor = delta > 0 ? 1 + ZOOM_STEP : 1 / (1 + ZOOM_STEP);
            const newScale = scale * zoomFactor;

            // Apply zoom constraints
            if (newScale < MIN_SCALE || newScale > MAX_SCALE) return;

            // Calculate new position to zoom at mouse point
            posX = mouseX - (mouseX - posX) * zoomFactor;
            posY = mouseY - (mouseY - posY) * zoomFactor;
            scale = newScale;

            updateTransform();
        });

        // Handle mouse down for panning
        playerContainer.addEventListener('mousedown', function(e) {
            if (scale <= 1) return;

            e.preventDefault();
            startX = e.clientX;
            startY = e.clientY;
            startPosX = posX;
            startPosY = posY;
            isPanning = true;
            playerContainer.style.cursor = 'grabbing';
        });

        // Handle mouse move for panning
        window.addEventListener('mousemove', function(e) {
            if (!isPanning) return;

            posX = startPosX + (e.clientX - startX);
            posY = startPosY + (e.clientY - startY);
            updateTransform();
        });

        // Handle mouse up to stop panning
        window.addEventListener('mouseup', function() {
            isPanning = false;
            playerContainer.style.cursor = 'grab';
        });

        // Handle double click to reset
        playerContainer.addEventListener('dblclick', resetZoomAndPosition);

        // Zoom buttons functionality
        zoomInBtn.addEventListener('click', function() {
            if (scale >= MAX_SCALE) return;

            const zoomFactor = 1 + ZOOM_STEP;
            const newScale = scale * zoomFactor;

            // Calculate center point zoom
            const containerWidth = playerContainer.offsetWidth;
            const containerHeight = playerContainer.offsetHeight;
            const centerX = containerWidth / 2;
            const centerY = containerHeight / 2;

            posX = centerX - (centerX - posX) * zoomFactor;
            posY = centerY - (centerY - posY) * zoomFactor;
            scale = newScale > MAX_SCALE ? MAX_SCALE : newScale;

            updateTransform();
        });

        zoomOutBtn.addEventListener('click', function() {
            if (scale <= MIN_SCALE) return;

            const zoomFactor = 1 / (1 + ZOOM_STEP);
            const newScale = scale * zoomFactor;

            // Calculate center point zoom
            const containerWidth = playerContainer.offsetWidth;
            const containerHeight = playerContainer.offsetHeight;
            const centerX = containerWidth / 2;
            const centerY = containerHeight / 2;

            posX = centerX - (centerX - posX) * zoomFactor;
            posY = centerY - (centerY - posY) * zoomFactor;
            scale = newScale < MIN_SCALE ? MIN_SCALE : newScale;

            updateTransform();
        });

        zoomResetBtn.addEventListener('click', resetZoomAndPosition);

        // Set initial cursor
        playerContainer.style.cursor = 'grab';

        // Add touch support for mobile devices
        let lastTouchDistance = 0;

        playerContainer.addEventListener('touchstart', function(e) {
            if (e.touches.length === 2) {
                // Store initial touch positions for pinch-zoom
                const touch1 = e.touches[0];
                const touch2 = e.touches[1];
                lastTouchDistance = Math.hypot(
                    touch2.clientX - touch1.clientX,
                    touch2.clientY - touch1.clientY
                );
            } else if (e.touches.length === 1 && scale > 1) {
                // Start panning with one finger if zoomed in
                const touch = e.touches[0];
                startX = touch.clientX;
                startY = touch.clientY;
                startPosX = posX;
                startPosY = posY;
                isPanning = true;
            }
        });

        playerContainer.addEventListener('touchmove', function(e) {
            e.preventDefault();

            if (e.touches.length === 2) {
                // Handle pinch-zoom
                const touch1 = e.touches[0];
                const touch2 = e.touches[1];
                const currentDistance = Math.hypot(
                    touch2.clientX - touch1.clientX,
                    touch2.clientY - touch1.clientY
                );

                if (lastTouchDistance > 0) {
                    const touchDelta = currentDistance - lastTouchDistance;
                    const zoomFactor = touchDelta > 0 ? 1.02 : 0.98;
                    const newScale = scale * zoomFactor;

                    if (newScale >= MIN_SCALE && newScale <= MAX_SCALE) {
                        // Calculate center of pinch
                        const centerX = (touch1.clientX + touch2.clientX) / 2 - playerContainer.getBoundingClientRect().left;
                        const centerY = (touch1.clientY + touch2.clientY) / 2 - playerContainer.getBoundingClientRect().top;

                        posX = centerX - (centerX - posX) * zoomFactor;
                        posY = centerY - (centerY - posY) * zoomFactor;
                        scale = newScale;

                        updateTransform();
                    }
                }

                lastTouchDistance = currentDistance;

            } else if (e.touches.length === 1 && isPanning) {
                // Handle panning with one finger
                const touch = e.touches[0];
                posX = startPosX + (touch.clientX - startX);
                posY = startPosY + (touch.clientY - startY);
                updateTransform();
            }
        });

        playerContainer.addEventListener('touchend', function() {
            isPanning = false;
            lastTouchDistance = 0;
        });
    }, 1000);  // Wait for 1 second to ensure all elements are loaded
    """

    # Display the HTML and execute the JavaScript
    display(HTML(html_content))
    display(Javascript(js_code))

    print(f"Video '{filename}' loaded successfully.")
    print("You can now zoom in/out using your mouse wheel or the zoom buttons.")
    print("Click and drag to pan when zoomed in, and double-click to reset the view.")

# Display initial instructions
print("Click the 'Upload Video' button to select and upload a video file.")
print("After uploading, you can zoom in/out the video without losing quality.")

Please upload a video file...


Saving ChatGPT creator is now worried about AI.mp4 to ChatGPT creator is now worried about AI.mp4


<IPython.core.display.Javascript object>

Video 'ChatGPT creator is now worried about AI.mp4' loaded successfully.
You can now zoom in/out using your mouse wheel or the zoom buttons.
Click and drag to pan when zoomed in, and double-click to reset the view.
